In [1]:
import pandas as pd
import numpy as np
#import twint
import nest_asyncio
nest_asyncio.apply()
import re

pd.options.display.max_rows = 999
pd.options.display.max_columns=999

from datetime import datetime

from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

from sklearn.linear_model import LinearRegression

# Import locally modified twint scraper
import os
import sys
module_path = os.path.abspath(os.path.join('C:/Users/Documents/JHU/SocialMediaAnalytics/final_project/'))
if module_path not in sys.path:
    sys.path.append(module_path)
from twint_local.twint import Config, run, storage

C:\Users\katon\AppData\Roaming\Python\Python38\site-packages\pandas\core\computation\expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
C:\Users\katon\AppData\Roaming\Python\Python38\site-packages\scipy\__init__.py:138: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.4)
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion} is required for this version of "


In [2]:
path = "C:/Users/Katon/Documents/JHU/SocialMediaAnalytics/final_project/data/"

data = pd.read_csv(path+"final_dataset.csv")
data.head()

State  Branch     Type Election_Date Party       Candidate  Win   Votes  \
0  Alabama  Senate  General    2022-11-08     R     Katie Britt    1  940054   
1  Alabama  Senate  General    2022-11-08     D       Will Boyd    0  435431   
2  Alabama  Senate  Primary    2022-05-24     D   Brandaun Dean    0   32863   
3  Alabama  Senate  Primary    2022-05-24     R    Jake Schafer    0    6951   
4  Alabama  Senate  Primary    2022-05-24     R  Karla DuPriest    0    5366   

   Incumbent           Handle  \
0          1  KatieBrittforAL   
1          0    willboydforAL   
2          0     BrandaunDean   
3          0        NO_HANDLE   
4          0        NO_HANDLE   

                                                 Bio  Following  Followers  \
0  Unapologetically committed putting AlabamaFirs...          2      19798   
1  Senate Nominee Husband Father Bishop Pastor En...       2224       4176   
2  Black America reparations I justice system pol...        207       2618   
3                                               None          0          0   
4                                               None          0          0   

   Bio_Length  bio_polarity  bio_subjectivity  bio_profanity  num_tweets  \
0          20      0.800000          0.750000       0.019468         965   
1           9      0.000000          0.000000       0.016661         330   
2          16     -0.166667          0.433333       0.076919        1602   
3           0           NaN               NaN            NaN           0   
4           0           NaN               NaN            NaN           0   

   mean_tweet_length  mean_unique_words  mean_pct_unique  mean_tweet_polarity  \
0          31.377202          28.131606         0.896562             0.228550   
1          30.869697          26.990909         0.874350             0.189708   
2          22.825843          20.606987         0.902792             0.012198   
3           0.000000           0.000000         0.000000             0.000000   
4           0.000000           0.000000         0.000000             0.000000   

   std_tweet_polarity  mean_tweet_subjectivity  std_tweet_subjectivity  \
0            0.298075                 0.443566                0.274657   
1            0.253048                 0.352834                0.298292   
2            0.242736                 0.345183                0.288341   
3            0.000000                 0.000000                0.000000   
4            0.000000                 0.000000                0.000000   

   mean_tweet_profanity  std_tweet_profanity  polarity_coef  \
0              0.038216             0.049209   1.830000e-05   
1              0.030553             0.034297   1.089450e-04   
2              0.178219             0.268846  -4.250000e-07   
3              0.000000             0.000000   0.000000e+00   
4              0.000000             0.000000   0.000000e+00   

   subjectivity_coef  profanity_coef  unique_coef  length_coef  \
0          -0.000006       -0.000002    -0.000503    -0.001155   
1           0.000255       -0.000030     0.010422     0.009264   
2          -0.000033        0.000008    -0.003128    -0.003749   
3           0.000000        0.000000     0.000000     0.000000   
4           0.000000        0.000000     0.000000     0.000000   

   pct_unique_coef  
0         0.000015  
1         0.000046  
2         0.000017  
3         0.000000  
4         0.000000

In [3]:
data['Election_Date'] = data['Election_Date'].astype(str)

In [4]:
def get_tweets_df(username, date):
    c = Config()
    c.Username = username
    c.Pandas = True
    #c.Limit = 3000
    c.User_full = True
    c.Since = date[0:3] + "1" + date[4:]
    c.Until = date
    run.Search(c)
    tweets_df = storage.panda.Tweets_df
    
    return storage.panda.Tweets_df

In [5]:
def get_unique_words(df):
    print(df.shape)
    tweets = df['tweet']
    
    unique_words = []
    lengths = []
    pct_unique = []
    for tweet in tweets:
        tweet_list = [word for word in word_tokenize(tweet) if word.isalnum()]
        lengths.append(len(tweet_list))
        unique_words.append(len(np.unique(tweet_list)))
        if len(tweet_list) != 0:
            pct_unique.append(len(np.unique(tweet_list)) / (len(tweet_list)))
        else:
            pct_unique.append(0)
    
    unique_reg = LinearRegression().fit(np.array(range(len(unique_words))).reshape(-1,1), np.array(unique_words))
    length_reg = LinearRegression().fit(np.array(range(len(lengths))).reshape(-1,1), np.array(lengths))
    pct_unique_reg = LinearRegression().fit(np.array(range(len(pct_unique))).reshape(-1,1), np.array(pct_unique))
    
    return unique_reg.coef_[0], length_reg.coef_[0], pct_unique_reg.coef_[0]
        

In [11]:
get_unique_words(get_tweets_df("DrNikiThran", '2022-08-09'))

1554120420034494464 2022-08-01 08:02:36 -0800 <DrNikiThran> This is why I still feel the Bern! @SenSanders
1544467492634071044 2022-07-05 16:45:19 -0800 <DrNikiThran> I actually enjoy live debating! Thanks CCTV for hosting us. US  Senate - Democratic Primary Debate - 7/5/2022  https://t.co/xBagCRHOwO via @YouTube  #DrThranCan #USSenate2022
1540422982396510213 2022-06-24 12:53:53 -0800 <DrNikiThran> ACEP // Emergency Physicians Deeply Concerned by Laws that Interfere with the Physician-Patient Relationship  https://t.co/GMTvW2J4Kt #DrThranCan #acep
1536507788347711488 2022-06-13 17:36:18 -0800 <DrNikiThran> Thanks Windsor Dems! Vermont Candidates for US Senate Forum-hosted by Windsor County Democrat...  https://t.co/tVzGq16lfa via @YouTube
1535282824479113217 2022-06-10 08:28:44 -0800 <DrNikiThran> Thanks to everyone who made this possible.    Debate - Vermont Democrats for the U.S. Senate  https://t.co/EZlrbGnnH2 via @YouTube #drthrancan
1527345383235801089 2022-05-19 10:48:10 -0800 <D

(0.2985294117647057, 0.3867647058823529, -0.0031079981399674494)

In [6]:
data['pct_unique'] = 0         #30
data['unique_coef'] = 0          #31
data['length_coef'] = 0   #32
data['pct_unique_coef'] = 0 # 33

for i in range(273, data.shape[0]):
    print("******************************", i, "******************************")
    handle = data.iloc[i, 9]
    if handle not in ("NO_HANDLE", "SUSPENDED"):
        date = data.iloc[i, 3]
        df = get_tweets_df(handle, date)
        if df.shape[0] == 0: # if no tweets, run again from general election day
            df = get_tweets_df(handle, '2022-11-08')
        if df.shape[0] != 0: # if still no tweets, skip user
            unique_coef, length_coef, pct_unique_coef = get_unique_words(df)
            data.iloc[i, 31] = unique_coef
            data.iloc[i, 32] = length_coef
            data.iloc[i, 33] = pct_unique_coef
            

****************************** 273 ******************************
1556009978577682432 2022-08-06 13:11:02 -0800 <PeterWelch> On the 57th anniversary of the Voting Rights Act, we remember the hard work of civil rights activists to secure voting rights for Black Americans.  Today, that fight continues as we work to end voter suppression and strengthen our democracy. We won't give up. Onward.  https://t.co/XAcNYY00et
1555665952892665856 2022-08-05 14:24:00 -0800 <PeterWelch> This is big news for our dairy farms: when Danone abruptly pulled out of our region, Organic Valley stepped up to the plate to help.   These farms are the heart of Vermont, and it’s great to see this new partnership form to keep them thriving.  https://t.co/rbGketSCq1
1555293253142040576 2022-08-04 13:43:02 -0800 <PeterWelch> William Clarence Matthews was a legend of Vermont sports and a pioneer for civil rights. I’d encourage all who can to get out to the game and learn a bit about his legacy.  https://t.co/0xa5Ixqa7

1547288755953868802 2022-07-13 11:36:01 -0800 <PeterWelch> I agree @POTUS. Assault weapons have no place on our streets.   We must use every tool available to end gun violence. That includes restoring the assault weapons ban.  https://t.co/hEGVyoPzTd
1547273407372447748 2022-07-13 10:35:01 -0800 <PeterWelch> Here's the deal: working families are struggling to pay their bills while corporate profits soar. That's unacceptable.   We need to tackle corporate greed with anti-trust laws to rein in monopolies and a Windfall Profits Tax on profits from price gouging.  https://t.co/69xbhKTfsV
1547241702901092357 2022-07-13 08:29:02 -0800 <PeterWelch> I agree @RepRoKhanna. Drug prices are unacceptably high. We need to act to save families money, not burden them with high costs. Glad to be your partner in this fight.
1546958327833313280 2022-07-12 13:43:01 -0800 <PeterWelch> Climate action can’t wait. Temperatures are rising and our aging electric grid is failing.   We need to clean up our power 

1539372088837955585 2022-06-21 15:18:00 -0800 <PeterWelch> It's so important to listen and learn from Ruby's story. Poll workers do essential work for our democracy. They deserve safety and respect — not harassment and violent threats.
1538951319465107457 2022-06-20 11:26:01 -0800 <PeterWelch> The Fairbanks Museum is a special place that adds so much to the St. Johnsbury community. It’s a privilege to help them secure federal funding to use sustainable building practices to construct the Tang Science Annex and offer a space for hands-on learning to all visitors.  https://t.co/iN7XOgMC0g
1538529286176768000 2022-06-19 07:29:00 -0800 <PeterWelch> On Juneteenth, we celebrate the effective end of slavery in the United States, honor Black history, and reaffirm our commitment to ending racism in America.   For those looking to mark the holiday in Vermont, the Burlington Free Press has a helpful guide.  https://t.co/6D5d1CT2Xj
1537918510856187906 2022-06-17 15:02:00 -0800 <PeterWelch> Our tea

1529887605575364608 2022-05-26 11:10:03 -0800 <PeterWelch> This is a big deal. I'd urge all Vermonters who are interested to sign up for this essential discussion on reducing hunger in the United States. To join a regional listening session, click here:  https://t.co/eHQthGoxVi
1529226899238551557 2022-05-24 15:24:39 -0800 <PeterWelch> Every day, we make a choice about the kind of country we want to live in. This nightmare is not what any of us would choose. We must come together to take action.
1529226898001346563 2022-05-24 15:24:38 -0800 <PeterWelch> To my colleagues standing in the way of effective and comprehensive gun violence prevention: what is the purpose of government if not to keep its citizens – its children – safe?
1529226896512524289 2022-05-24 15:24:38 -0800 <PeterWelch> No one should have to experience the kind of loss or bear the kind of pain that the community of Uvalde is facing today.   I am heartbroken and angry. This country’s refusal to take action to prevent gun

1521950311098822663 2022-05-04 13:30:05 -0800 <PeterWelch> May is #AAPIHeritageMonth, a chance to celebrate the history and achievements of Asian Americans and Pacific Islanders and an opportunity to recommit to the fight against anti-AAPI hate. To learn more, visit:   https://t.co/JuBrcay6xG
1521914820630663177 2022-05-04 11:09:03 -0800 <PeterWelch> Without Roe, the unthinkable becomes possible: a nationwide ban on abortion.   Most Americans believe abortion should be legal. But the rules of the Senate don't allow majority rule. That has to change.   It's time to abolish the filibuster and codify Roe.  https://t.co/jpCbrYb4N4
1521901481783345152 2022-05-04 10:16:03 -0800 <PeterWelch> This program is critical to help more VTers access the services that have helped Mistee and others get their lives back.   I secured funding for this life-saving program, and we will keep up the fight to fund effective treatment for substance use disorder.  https://t.co/TwDboP0LaK
1521552695341027329 2022

...

1438949254492528644 2021-09-17 12:33:31 -0800 <NelsonforWI> Addendum: We donated all the unopened snacks. They’d been sitting in our pantry. When you have two young kids and you’re running a campaign, you buy a whole lot of food. I still don’t know where the Funyuns came from, though.
1438922413450878976 2021-09-17 10:46:51 -0800 <NelsonforWI> My family quit Frito-Lay snacks and has been boycotting Nabisco.   Given Mondelez's attempts to squash their striking workers, I'm clearing out my pantry. Corporate monopolies are starving this country.  Help striking workers here:  https://t.co/LEjODc42oM  #NoContractsNoSnacks  https://t.co/Eqlle5Mk3o
1438579224282116097 2021-09-16 12:03:09 -0800 <NelsonforWI> @Super70sSports Could not agree more.
1438540635687079937 2021-09-16 09:29:48 -0800 <NelsonforWI> Ah yes. The halcyon days of my youth. Now I know where the picture from my 9 year-old birthday party landed.
1438466720822398981 2021-09-16 04:36:06 -0800 <NelsonforWI> Must read. Aisha is an 

1435734392543055873 2021-09-08 15:38:48 -0800 <NelsonforWI> Here in Jefferson County, people are deeply worried about the climate crisis and weather disasters taking place across the country.  https://t.co/hCseJ4KcIO
1435714058540437506 2021-09-08 14:18:00 -0800 <NelsonforWI> Thank you for the kind post. Next time we’ll do a listening session at your coffee shop!
1435679477833601036 2021-09-08 12:00:35 -0800 <NelsonforWI> My third stop of the day was in Columbia County. Health care issues were very important to these residents.  We need #MedicareForAll now!  https://t.co/F8mjEews3C
1435676828627316739 2021-09-08 11:50:04 -0800 <NelsonforWI> We must tax the rich — and make sure they actually pay those taxes.   If you or I evaded taxes like this, we’d be in big trouble. Billionaires who don’t pay taxes just get lobbyists to make it legal.  https://t.co/Cq5T9sQ0YE
1435664456156127233 2021-09-08 11:00:54 -0800 <NelsonforWI> It was great to meet with Baraboo Mayor Rob Nelson!  I had the cha

1433125318571724801 2021-09-01 10:51:16 -0800 <NelsonforWI> The Supreme Court’s endorsement of the horrific new abortion bounty hunt law in Texas makes it clear:  Democrats must end the filibuster, codify a national right to abortion, and expand the Supreme Court.  Every right we cherish hangs in the balance.
1432894953814994944 2021-08-31 19:35:53 -0800 <NelsonforWI> From Big Ag to Amazon to health care to private equity crushing local newspapers, I’m hearing every single day about how corporate consolidation is hurting people all across Wisconsin.   Fighting this decades-long trend will be one of my top priorities in the Senate.  https://t.co/phLY9AxjMh
1432822468801093637 2021-08-31 14:47:51 -0800 <NelsonforWI> Great talk with folks in Forest County about logging, the environment, and other issues facing the local community.  https://t.co/0R2BAExTou
1432795007841406979 2021-08-31 12:58:44 -0800 <NelsonforWI> Out here in NE Wisconsin, the phone reception is… well, it’s not good.   We

1430572277930807296 2021-08-25 09:46:24 -0800 <NelsonforWI> Thanks to the Portage County Dems and the Franklin Progressive Women’s Group for having me out to speak on Sunday!  https://t.co/rQRF6ZwUkr
1430310906538385408 2021-08-24 16:27:48 -0800 <NelsonforWI> Democrats in the Senate *must* do whatever it takes to pass both the John Lewis Act and the For The People Act. There is nothing more urgent than saving our democracy.  If they break their promises and choose the filibuster over democracy, it will be a historic shame.
1430212967723933700 2021-08-24 09:58:38 -0800 <NelsonforWI> On Saturday, a right-wing moron told one of my volunteers that we deserved to be shot in the head.  Republicans like @SenRonJohnson who hype up lies &amp; incite violence are responsible.  It won’t intimidate us. Our tour of every Wisconsin county continues.  https://t.co/kNR2ghjIjd
1430167636210589706 2021-08-24 06:58:30 -0800 <NelsonforWI> Solid piece by John Nichols. Could not agree more. If it was not fo

1426941443910811649 2021-08-15 09:18:46 -0800 <NelsonforWI> Loved spending time with folks in Pierce, Eau Claire, Clark, Trempealeau, Buffalo, and Pepin Counties yesterday.  As I say here, I’m running for Senate because working folks across Wisconsin need someone to work for them, not billionaires and corporations.  https://t.co/zTaIAfXgPi
1426727927920660483 2021-08-14 19:10:19 -0800 <NelsonforWI> We’re known for our dairy but Wisconsin produces some of the best — and tallest — corn in the country, too.   As we close another day of the statewide Full Nelson Tour, I’m doubling down on my promise to fight for family farmers against Big Ag and corporate interests.  https://t.co/3gykFdhToo
1426718627785498624 2021-08-14 18:33:22 -0800 <NelsonforWI> There were Democrats and Republicans sitting together at Lost Pirate Tiki Bar in Buffalo County, proving that there’s we can all agree on some issues — and a good beer  https://t.co/a9Lyz22Oau
1426695031105130502 2021-08-14 16:59:36 -0800 <Nels

In [9]:
data.to_csv(path+'final_unique_data_checkpoint2.csv')

In [8]:
data

State  Branch     Type Election_Date Party  \
0           Alabama  Senate  General    2022-11-08     R   
1           Alabama  Senate  General    2022-11-08     D   
2           Alabama  Senate  Primary    2022-05-24     D   
3           Alabama  Senate  Primary    2022-05-24     R   
4           Alabama  Senate  Primary    2022-05-24     R   
5           Alabama  Senate  Primary    2022-05-24     R   
6           Alabama  Senate  Primary    2022-05-24     D   
7           Alabama  Senate  Primary    2022-05-24     R   
8           Alabama  Senate  Primary    2022-05-24     R   
9           Alabama  Senate  Primary    2022-05-24     R   
10          Alabama  Senate  Primary    2022-05-24     D   
11           Alaska  Senate  General    2022-11-08     R   
12           Alaska  Senate  General    2022-11-08     R   
13           Alaska  Senate  Primary    2022-08-16     R   
14           Alaska  Senate  Primary    2022-08-16     R   
15           Alaska  Senate  Primary    2022-08-16     R   
16           Alaska  Senate  Primary    2022-08-16     D   
17          Arizona  Senate  General    2022-11-08     R   
18          Arizona  Senate  General    2022-11-08     D   
19          Arizona  Senate  Primary    2022-08-02     R   
20          Arizona  Senate  Primary    2022-08-02     R   
21          Arizona  Senate  Primary    2022-08-02     R   
22          Arizona  Senate  Primary    2022-08-02     R   
23          Arizona  Senate  Primary    2022-08-02     R   
24         Arkansas  Senate  General    2022-11-08     R   
25         Arkansas  Senate  General    2022-11-08     D   
26         Arkansas  Senate  Primary    2022-05-24     D   
27         Arkansas  Senate  Primary    2022-05-24     R   
28         Arkansas  Senate  Primary    2022-05-24     D   
29         Arkansas  Senate  Primary    2022-05-24     R   
30         Arkansas  Senate  Primary    2022-05-24     R   
31         Arkansas  Senate  Primary    2022-05-24     R   
32         Arkansas  Senate  Primary    2022-05-24     D   
33       California  Senate  General    2022-11-08     D   
34       California  Senate  General    2022-11-08     R   
35       California  Senate  Primary    2022-06-07     D   
36       California  Senate  Primary    2022-06-07     R   
37       California  Senate  Primary    2022-06-07     R   
38       California  Senate  Primary    2022-06-07     R   
39       California  Senate  Primary    2022-06-07     R   
40       California  Senate  Primary    2022-06-07     R   
41         Colorado  Senate  General    2022-11-08     R   
42         Colorado  Senate  General    2022-11-08     D   
43         Colorado  Senate  Primary    2022-06-07     R   
44         Colorado  Senate  Primary    2022-06-07     R   
45      Connecticut  Senate  General    2022-11-08     R   
46      Connecticut  Senate  General    2022-11-08     D   
47      Connecticut  Senate  Primary    2022-08-09     R   
48      Connecticut  Senate  Primary    2022-08-09     R   
49      Connecticut  Senate  Primary    2022-08-09     R   
50          Florida  Senate  General    2022-11-08     R   
51          Florida  Senate  General    2022-11-08     D   
52          Florida  Senate  Primary    2022-08-23     D   
53          Florida  Senate  Primary    2022-08-23     D   
54          Florida  Senate  Primary    2022-08-23     D   
55          Florida  Senate  Primary    2022-08-23     D   
56          Georgia  Senate  General    2022-11-08     R   
57          Georgia  Senate  General    2022-11-08     D   
58          Georgia  Senate  Primary    2022-05-24     R   
59          Georgia  Senate  Primary    2022-05-24     R   
60          Georgia  Senate  Primary    2022-05-24     R   
61          Georgia  Senate  Primary    2022-05-24     R   
62          Georgia  Senate  Primary    2022-05-24     R   
63          Georgia  Senate  Primary    2022-05-24     R   
64          Georgia  Senate  Primary    2022-05-24     D   
65          Georgia  Senate  Primary    2022-05-24    